In [1]:
# encoding: utf-8
# Original code from https://gist.github.com/nathanielatom/6442f94faca69dcf6efae146cb66c30c

In [1]:
import bokeh.models as bkm
import resampy
from bokeh.plotting import figure, output_file, show
from bokeh.layouts import layout
from BokehAudioPlayer import AudioPlayerModel
import base64
from io import BytesIO
import numpy as np
from scipy.io import wavfile
import pandas as pd
from bokeh import palettes

from bokeh.io import output_notebook
output_notebook()


/Users/russell/anaconda/lib/python3.5/site-packages/numba/errors.py:102: UserWarning: Insufficiently recent colorama version found. Numba requires colorama >= 0.3.9
  warnings.warn(msg)


Loading BokehJS ...

## First, lets sonify the seismic background noise

The band at ~0.05 Hz is the primary microseism due to ocean waves hitting the coastline. The peak at 0.1-0.2 Hz is the secondary microseism.

In [2]:
# Load data
datadir = '../data/'
datastr = 'P39A_noise_BHZ'
TargetDurations = [3,8]  # seconds

tabs = []
for ii, TargetDuration in enumerate(TargetDurations):

    datafile = datadir+datastr+'.csv'
    outfile = './'

    # Load seismogram into dataframe
    # df = pd.read_csv(datafile, names=['data'])
    df = pd.read_csv(datafile, parse_dates=['time'], index_col='time')
    dt = df.t[1]-df.t[0]  # time between samples
    fs = 1/dt  # [Hz] sample rate

    # Seismic data in units of displacement
    data = np.asarray(df.data)*1e3  # convert meters to millimeters
    data_dis = data

    # 1) force the signal's mean value to be zero (to protect your loudspeakers...)
    data = data - np.mean(data)

    # 2) limit the signal's amplitude = avoid too large peaks (how to re-kill your loudspeakers...)
    # a simple way is to normalize the data according to its maximum amplitude value
    # data = data/np.amax(data) # This is dangerous, peak values can be negative, too
    # better to do it THIS way:  
    data = data/np.amax(np.absolute(data))

    # Set up title names
    default_title=datastr  # will become output file name
    title='Background Seismic Noise at P39A'
    plot_filename=default_title + '_' + str(TargetDuration) + 's'
    
    # make plot and sonify
    # grid = AudioPlayerModel.sonify_plotwf(data=data,data_dis=data_dis,fs=fs,TargetDuration=TargetDuration,
    #                                       fs_resamp=44100,default_title=default_title,title=title)
    grid = AudioPlayerModel.sonify_plotwfspec(data=data,data_dis=data_dis,fs=fs,TargetDuration=TargetDuration,
                                          fs_resamp=44100,default_title=default_title,title=title,
                                          aspect_ratio=2,  # aspect ratio of individual plots
                                          # palette='RdYlBu11'
                                          palette = palettes.all_palettes['Magma'][256],
                                          seek_bar_color='limegreen',
                                          seek_bar_alpha=0.8,
                                          # palette='Viridis256'
                                          )                                      
    # Build tabs for different waveforms
    tab = bkm.Panel(child=grid, title=str(TargetDuration) + ' seconds')
    tabs.append(tab)

# Combine tabs in final plot
plot = bkm.Tabs(tabs=tabs)
show(plot)


output_file(outfile+plot_filename+'.html')


In [3]:
# Load data
datadir = '../data/'

# datastrs = ['TRQA_M9.1_BHZ', 'P39A_M9.1_BHZ', 'MAJO_M9.1_BHZ']
# titlestr = 'M9.1, Tohoku Japan March 11, 2011 ('
# dist_km = [17900, 9700, 416]

datastrs = ['TRQA_M7.3_BHZ', 'P39A_M7.3_BHZ', 'MAJO_M7.3_BHZ']
titlestr = 'M7.3, Tohoku Japan March 9, 2011 ('
dist_km = [17900, 9700, 416]


tabs = []
for ii, datastr in enumerate(datastrs):

    datafile = datadir+datastr+'.csv'
    outfile = './'
    TargetDuration = 3  # seconds

    # Load seismogram into dataframe
    # df = pd.read_csv(datafile, names=['data'])
    df = pd.read_csv(datafile, parse_dates=['time'], index_col='time')
    dt = df.t[1]-df.t[0]  # time between samples
    fs = 1/dt  # [Hz] sample rate

    # Seismic data in units of displacement
    data = np.asarray(df.data)*1e3  # convert meters to millimeters
    data_dis = data

    # 1) force the signal's mean value to be zero (to protect your loudspeakers...)
    data = data - np.mean(data)

    # 2) limit the signal's amplitude = avoid too large peaks (how to re-kill your loudspeakers...)
    # a simple way is to normalize the data according to its maximum amplitude value
    # data = data/np.amax(data) # This is dangerous, peak values can be negative, too
    # better to do it THIS way:  
    data = data/np.amax(np.absolute(data))

    # Set up title names
    default_title=datastr  # will become output file name
    title=titlestr+' '+datastr[:4]+' '+str(dist_km[ii])+' km from source)'
    
    # make plot and sonify
    # grid = AudioPlayerModel.sonify_plotwf(data=data,data_dis=data_dis,fs=fs,TargetDuration=TargetDuration,
    #                                       fs_resamp=44100,default_title=default_title,title=title)
    grid = AudioPlayerModel.sonify_plotwfspec(data=data,data_dis=data_dis,fs=fs,TargetDuration=TargetDuration,
                                          fs_resamp=44100,default_title=default_title,title=title,
                                          aspect_ratio=2,  # aspect ratio of individual plots
                                          # palette='RdYlBu11'
                                          palette = palettes.all_palettes['Magma'][256],
                                          seek_bar_color='limegreen',
                                          seek_bar_alpha=0.8,
                                          # palette='Viridis256'
                                          )                                      
    # Build tabs for different waveforms
    tab = bkm.Panel(child=grid, title=datastr)
    tabs.append(tab)

# Combine tabs in final plot
plot = bkm.Tabs(tabs=tabs)

plot_filename='.'.join(datastrs) + '_' + str(TargetDuration) + 's'
output_file(outfile+plot_filename+'.html')

show(plot)